In [73]:
# Load in necesarry libs

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import json
import re
import string
import copy

import collections
from collections import Counter

from ingredient_parser import en

from pprint import pprint

import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords

In [74]:
# Load in ingredients KB

with open("ingredients_kb.json", 'r') as infile:
    ingredients_kb = json.load(infile)


In [75]:
# Function to load in recipes for analysis 

# contains significant amount of info per recipe - needs to be cleaned before working with
df_rec = pd.read_json("../allrecipes-recipes.json",lines=True)

# simple - contains cusinse and recipes
df_rec_2 = pd.read_json("train.json")

In [116]:
# try filtering out pizza
df_rec = df_rec[~df_rec['description'].str.contains('pizza')]



In [99]:
# Uncomment to see column values

print(df_rec.columns)
print(df_rec_2.columns)

Index(['author', 'cook_time_minutes', 'description', 'error', 'footnotes',
       'ingredients', 'instructions', 'photo_url', 'prep_time_minutes',
       'rating_stars', 'review_count', 'time_scraped', 'title',
       'total_time_minutes', 'url'],
      dtype='object')
Index(['cuisine', 'id', 'ingredients'], dtype='object')


In [142]:
# Create Dataframes for helathy / unhealthy and veg/non veg ingredients

df_veg = df_rec[df_rec['description'].str.contains('vegetarian')]
df_non_veg = df_rec[~df_rec['description'].str.contains('vegetarian')]
df_health = df_rec[df_rec['description'].str.contains('healthy|low-calorie|low calorie|low-carb|low carb|fat-free|weightloss|weight-loss')]
df_unhealthy = df_rec[~df_rec['description'].str.contains('healthy|low-calorie|low calorie|low-carb|low carb|fat-free|weightloss|weight-loss')]

# To Do - consider shuffling larger lists if slow

In [132]:
# Increase amount of healthy recipes by looking for additional search terms

#df_health_1 = df_rec[df_rec['description'].str.contains('healthy|low-calorie')]
#df_health_2 = df_rec[df_rec['description'].str.contains('low-fat')]
# df_health_3 = df_rec[df_rec['description'].str.contains('weight-loss')]



In [144]:
print(df_health.shape)
print(df_unhealthy.shape)

(2124, 15)
(88302, 15)


In [143]:
# Uncomment to see shapes

print(df_veg.shape,df_non_veg.shape)
print(df_health.shape,df_unhealthy.shape)

(791, 15) (89635, 15)
(2124, 15) (88302, 15)


In [152]:
df_unhealthy = df_unhealthy.sample(n=2124)

In [81]:
 # Shuffle larger datasets to match other shapes

In [82]:
# Make simple list from unfiltered ingredients

def simple_list_full_rec(df,col_string):
    ingredients = []
    
    # iterate through all lists in df
    for raw_ings in df[col_string].tolist():
        #print(raw_ings)
        # iterate through each ingredient description
        for raw in raw_ings:
            # parse only the name using our parser
            raw_dict = en.parse(raw)
            #print(raw_dict['name'])
            ingredients.append(raw_dict['name'])
            
    # return the cleaned ingredients 
    return ingredients

In [83]:
veg_ing = simple_list_full_rec(df_veg,'ingredients')
non_veg_ing = simple_list_full_rec(df_non_veg,'ingredients')

healthy_ing = simple_list_full_rec(df_health,'ingredients')
unhealthy_ing = simple_list_full_rec(df_unhealthy,'ingredients')


In [84]:
# Make italian simple list function 

def simple_list_from_df(df,col_string):
    ingredients = []
    for i in italian_df[col_string].tolist():
        for j in i:
            italian += (j.lower().split())


In [85]:
# Helper function for KB comparison

def clean_text(s):
    tokens = word_tokenize(s)
    table = str.maketrans('', '', string.punctuation)
    stripped = [w.translate(table) for w in tokens]
    
    # remove remaining tokens that are not alphabetic
    words = [word for word in stripped if word.isalpha()]
    
    # filter out stop words
    stop_words = set(stopwords.words('english'))
    words = [w for w in words if not w in stop_words]
    words = [word for word in stripped if word.isalpha()]
    
    return words

In [150]:
# Function for comparing simple list against KB

def comp_to_kb(ing_list,ingredientsKB):
    ingredients = {}

    for category in ingredientsKB:
        counter = Counter()
        for ingredient in ing_list:
            tokens = clean_text(ingredient)
            # print(tokens)
            # try all permuations in tokens
            for perm in tokens:
                if perm in ingredientsKB[category]:
                    counter[perm] += 1
        if counter:
            ingredients[category] = counter
            
    return ingredients

In [151]:
test = df_non_veg.sample(n=5)
comp_to_kb(veg_ing,test)

['ounce', 'packages', 'frozen', 'chopped', 'broccoli']
['shredded', 'Cheddar', 'cheese']
['eggs', 'beaten']
['onion', 'minced']
['ounce', 'can', 'condensed', 'cream', 'of', 'mushroom', 'soup']
['mayonnaise']
['dry', 'bread', 'stuffing', 'mix']
['butter', 'melted']
['butter']
['mushrooms', 'chopped']
['fresh', 'shiitake', 'mushrooms', 'stemmed', 'and', 'coarsely', 'chopped']
['minced', 'garlic']
['dried', 'thyme']
['dried', 'rosemary', 'crushed']
['salt', 'to', 'taste']
['ground', 'black', 'pepper', 'to', 'taste']
['chicken', 'broth']
['baking', 'potatoes', 'scrubbed']
['Parmesan', 'cheese']
['heavy', 'cream']
['salt']
['ground', 'black', 'pepper']
['halfandhalf', 'cream']
['spaghetti']
['head', 'cauliflower', 'broken', 'into', 'small', 'florets']
['olive', 'oil']
['onion', 'chopped']
['garlic', 'minced']
['chopped', 'fresh', 'parsley']
['garlic', 'powder']
['salt', 'to', 'taste']
['ground', 'black', 'pepper', 'to', 'taste']
['grated', 'Parmesan', 'cheese']
['chopped', 'broccoli']
['cho

['eggs', 'beaten']
['vegetable', 'oil']
['onion', 'chopped']
['bay', 'leaf']
['garlic', 'minced']
['dried', 'split', 'peas']
['barley']
['salt']
['water']
['carrots', 'chopped']
['stalks', 'celery', 'chopped']
['potatoes', 'diced']
['chopped', 'parsley']
['dried', 'basil']
['dried', 'thyme']
['ground', 'black', 'pepper']
['cornstarch']
['water']
['soy', 'sauce']
['olive', 'oil']
['vegetable', 'oil']
['carrot', 'sliced']
['red', 'bell', 'pepper', 'chopped']
['zucchini', 'sliced']
['fresh', 'corn', 'kernels']
['crushed', 'garlic']
['green', 'onions', 'sliced']
['bean', 'sprouts']
['medium', 'potatoes', 'peeled']
['butter']
['salt']
['fresh', 'ground', 'black', 'pepper', 'to', 'taste']
['milk', 'warmed']
['kasha', 'toasted', 'buckwheat', 'groats']
['bulgar']
['minced', 'onion']
['garlic', 'minced']
['carrots', 'finely', 'chopped']
['sliced', 'mushrooms']
['allpurpose', 'flour']
['corn', 'kernels', 'blanched']
['olive', 'oil']
['onions', 'chopped']
['green', 'bell', 'pepper', 'chopped']
['

['brown', 'sugar']
['mild', 'curry', 'powder']
['dried', 'oregano']
['ground', 'cinnamon']
['ground', 'nutmeg']
['salt', 'and', 'pepper', 'to', 'taste']
['plain', 'yogurt']
['chopped', 'fresh', 'parsley', 'optional']
['cube', 'vegetable', 'bouillon']
['boiling', 'water']
['ketchup']
['vegetarian', 'Worcestershire', 'sauce']
['dry', 'mustard']
['dried', 'minced', 'onion', 'flakes']
['salt']
['white', 'sugar']
['cayenne', 'pepper', 'or', 'to', 'taste']
['vegetable', 'oil']
['slice', 'lemon']
['honey']
['garlic', 'minced']
['thinly', 'sliced', 'potatoes']
['frozen', 'green', 'beans']
['dried', 'thyme']
['ground', 'black', 'pepper']
['vegetarian', 'Worcestershire', 'sauce']
['vegetable', 'broth', 'divided']
['cornstarch']
['chopped', 'fresh', 'parsley']
['uncooked', 'white', 'rice']
['olive', 'oil']
['chopped', 'onion']
['garlic', 'chopped']
['chopped', 'celery']
['salt', 'and', 'pepper', 'to', 'taste']
['chopped', 'fresh', 'parsley']
['dried', 'basil']
['dried', 'oregano']
['dried', 'tarr

['chopped', 'fresh', 'parsley']
['ground', 'cumin']
['dried', 'marjoram']
['chili', 'powder']
['salt']
['spinach', 'fettuccine', 'pasta']
['extra', 'virgin', 'olive', 'oil']
['shallot', 'chopped']
['garlic', 'chopped']
['chopped', 'fresh', 'oyster', 'mushrooms']
['heavy', 'cream']
['chopped', 'fresh', 'sage']
['salt', 'and', 'pepper', 'to', 'taste']
['ounce', 'package', 'thin', 'spaghetti']
['sesame', 'oil']
['soy', 'sauce']
['cayenne', 'pepper']
['red', 'bell', 'pepper', 'julienned']
['bunch', 'fresh', 'cilantro', 'leaves', 'finely', 'chopped']
['butter']
['uncooked', 'orzo', 'pasta']
['minced', 'garlic']
['potatoes', 'peeled', 'and', 'diced']
['carrot', 'sliced']
['onion', 'chopped']
['dried', 'Italian', 'seasoning']
['salt', 'and', 'pepper', 'to', 'taste']
['water']
['cube', 'vegetable', 'bouillon']
['freshly', 'grated', 'Parmesan', 'cheese']
['ounce', 'package', 'farfalle', 'bow', 'tie', 'pasta']
['olive', 'oil']
['red', 'onion', 'chopped']
['garlic', 'minced']
['zucchini', 'choppe

['kelp', 'powder']
['garlic', 'powder']
['paprika']
['onion', 'powder', 'or', 'flakes']
['salt']
['olive', 'oil', 'as', 'needed']
['Tartar', 'Sauce']
['mayonnaise']
['dill', 'pickle', 'relish']
['fresh', 'lemon', 'juice']
['whole', 'wheat', 'hamburger', 'buns', 'split']
['sliced', 'almonds']
['butter']
['onion', 'finely', 'chopped']
['eggs', 'lightly', 'beaten']
['mayonnaise']
['ounce', 'can', 'condensed', 'cream', 'of', 'mushroom', 'soup']
['ounce', 'bags', 'frozen', 'chopped', 'broccoli', 'thawed', 'and', 'drained']
['salt', 'and', 'pepper', 'to', 'taste']
['sugar', 'pumpkin', 'top', 'removed', 'seeded']
['shredded', 'Cheddar', 'cheese']
['ounce', 'package', 'herb', 'seasoned', 'stuffing', 'mix']
['melted', 'butter']
['olive', 'oil']
['garlic', 'crushed']
['yellow', 'onion', 'chopped']
['carrot', 'chopped']
['ounce', 'can', 'golden', 'corn', 'drained']
['salt', 'and', 'pepper', 'to', 'taste']
['chicken', 'broth']
['ounce', 'can', 'white', 'beans']
['diced', 'fresh', 'tomatoes']
['dri

...

['lean', 'ground', 'beef']
['onion', 'grated']
['cooked', 'quinoa']
['milk']
['garlic', 'minced']
['egg', 'beaten']
['chopped', 'fresh', 'basil']
['chopped', 'fresh', 'oregano']
['red', 'pepper', 'flakes']
['salt', 'and', 'ground', 'black', 'pepper', 'to', 'taste']
['olive', 'oil']
['Pasta']
['olive', 'oil', 'or', 'to', 'taste']
['salt', 'to', 'taste']
['spaghetti', 'squash', 'halved', 'and', 'seeded']
['Sauce']
['olive', 'oil']
['onion', 'chopped']
['garlic', 'minced']
['red', 'pepper', 'flakes']
['sliced', 'fresh', 'mushrooms']
['green', 'bell', 'pepper', 'chopped']
['zucchini', 'sliced']
['ounce', 'can', 'sliced', 'black', 'olives']
['ounce', 'can', 'crushed', 'tomatoes']
['chopped', 'fresh', 'basil']
['chopped', 'fresh', 'oregano']
['honey']
['water']
['dry', 'lentils']
['onion', 'chopped']
['garlic', 'minced']
['paprika']
['bay', 'leaf']
['cumin', 'seeds', 'or', 'more', 'to', 'taste', 'ground']
['salt', 'and', 'ground', 'black', 'pepper', 'to', 'taste']
['olive', 'oil']
['head', '

['freshly', 'grated', 'ParmigianoReggiano', 'cheese']
['ribs', 'celery', 'chopped']
['leeks', 'chopped', 'and', 'divided']
['garlic', 'crushed', 'and', 'divided']
['slices', 'fresh', 'ginger', 'root']
['sea', 'salt', 'and', 'freshly', 'ground', 'black', 'pepper', 'to', 'taste']
['freshly', 'grated', 'nutmeg', 'or', 'to', 'taste']
['water']
['bay', 'leaves']
['fresh', 'rosemary', 'leaves', 'divided']
['ounce', 'piece', 'of', 'ParmigianoReggiano', 'rind']
['heavy', 'whipping', 'cream', 'or', 'as', 'needed']
['Broth']
['vegetable', 'stock']
['onion', 'peeled', 'and', 'halved']
['soy', 'sauce']
['garlic', 'coarsely', 'chopped']
['inch', 'cinnamon', 'sticks']
['ground', 'ginger']
['pods', 'star', 'anise']
['bay', 'leaves']
['Soup']
['ounce', 'package', 'thin', 'rice', 'noodles', 'such', 'as', 'Thai']
['vegetable', 'oil', 'or', 'as', 'needed']
['ounce', 'packages', 'firm', 'tofu', 'drained', 'and', 'cut', 'into', 'slices']
['enoki', 'mushrooms']
['scallions', 'thinly', 'sliced']
['coarsely',

['dried', 'oregano', 'or', 'to', 'taste']
['dried', 'basil', 'or', 'to', 'taste']
['salt']
['poultry', 'seasoning', 'or', 'to', 'taste']
['Filling']
['ounce', 'container', 'lowfat', 'ricotta', 'cheese']
['ounce', 'package', 'fresh', 'spinach']
['egg']
['grated', 'Parmesan', 'cheese']
['minced', 'garlic']
['ground', 'nutmeg']
['salt', 'and', 'ground', 'black', 'pepper', 'to', 'taste']
['canola', 'oil']
['eggs']
['allpurpose', 'flour']
['head', 'cauliflower', 'cut', 'into', 'florets']
['mayonnaise']
['lemon', 'juiced']
['olive', 'oil']
['eggplant', 'peeled', 'and', 'cut', 'into', 'slices']
['eggs', 'divided']
['Italian', 'bread', 'crumbs']
['ounce', 'container', 'ricotta', 'cheese']
['fresh', 'spinach']
['garlic', 'powder', 'or', 'to', 'taste']
['Italian', 'seasoning', 'or', 'to', 'taste']
['ounce', 'jar', 'garlic', 'and', 'onion', 'pasta', 'sauce', 'or', 'to', 'taste']
['ounce', 'package', 'shredded', 'mozzarella', 'cheese']
['inch', 'thick', 'slices', 'eggplant', 'rounds']
['salt']
['c

['vegetable', 'broth', 'such', 'as', 'Touch', 'of', 'Taste']
['sambal', 'oelek', 'chile', 'paste']
['whole', 'grain', 'bowtie', 'pasta']
['extravirgin', 'olive', 'oil']
['peeled', 'seeded', 'and', 'cubed', 'winter', 'squash']
['sweet', 'onion', 'diced']
['red', 'bell', 'pepper', 'diced']
['ounce', 'can', 'diced', 'tomatoes']
['fresh', 'green', 'beans', 'cut', 'into', 'pieces']
['pitted', 'kalamata', 'olives']
['minced', 'garlic']
['torn', 'fresh', 'spinach']
['red', 'wine', 'vinegar']
['white', 'sugar']
['minced', 'fresh', 'basil']
['sea', 'salt', 'or', 'to', 'taste']
['cracked', 'black', 'pepper', 'or', 'to', 'taste']
['grated', 'Parmesan', 'cheese']
['Spaghetti']
['ounce', 'jar', 'Pesto']
['salt']
['fresh', 'green', 'beans', 'trimmed']
['extra', 'large', 'zucchini', 'spiralized']
['extravirgin', 'olive', 'oil']
['grated', 'Parmesan', 'cheese']
['red', 'pepper', 'flakes', 'optional']
['toasted', 'pine', 'nuts']
['olive', 'oil']
['ground', 'beef']
['ounce', 'packet', 'taco', 'seasoning

{}

In [87]:
veg_ing_clean = comp_to_kb(veg_ing,ingredients_kb) # Currently slow

In [88]:
nonveg_ing_clean = comp_to_kb(non_veg_ing,ingredients_kb) # Currently slow

In [145]:
health_ing_clean = comp_to_kb(healthy_ing,ingredients_kb) # Currently slow

In [146]:
unhealth_ing_clean = comp_to_kb(unhealthy_ing,ingredients_kb) # Currently slow

In [91]:
#pprint(veg_ing_clean)
#pprint(health_ing_clean)

In [92]:
#pprint(veg_ing_clean)
#pprint(health_ing_clean)

In [105]:
def compare_ingredients(dict_1,dict_2):
    
    master_counter = []
    
    # Iterate through all keys in one diciontary
    for category in dict_1:
        
        # Check to see if key exists
        if category in dict_2.keys():
            
            #create a copy of the first counter
            cop = copy.deepcopy(dict_1[category])
            
            # subtract the two counters
            cop.subtract(dict_2[category])
            
            # print(single)
            
            # take absolute value of all ingredients
            #for ingredient in cop.keys():
            #    cop[ingredient] = abs(cop[ingredient])
                
            # add the abs diff counter to the master counter
            master_counter.append([category,cop])
        
        else:
            # account for case where entire group is not in the section dictionary
            master_counter.append([category,dict_1[category]]) 
    
    return master_counter
                        
        
        
            

In [147]:
health_diff_1 = compare_ingredients(unhealth_ing_clean,health_ing_clean)
health_diff_2 = compare_ingredients(health_ing_clean,unhealth_ing_clean)

health_diff_1.sort()
health_diff_2.sort()

In [148]:
pprint(health_diff_1)

[['alcoholicIngredients',
  Counter({'rum': 19,
           'wine': 17,
           'liqueur': 14,
           'vodka': 10,
           'brandy': 8,
           'beer': 7,
           'tequila': 7,
           'ale': 5,
           'bitters': 4,
           'whiskey': 4,
           'vermouth': 4,
           'sherry': 4,
           'sec': 4,
           'eggnog': 3,
           'schnapps': 2,
           'curacao': 1,
           'sake': 1,
           'cachaca': 1,
           'bourbon': 0,
           'champagne': 0,
           'campari': -1,
           'cacao': -4})],
 ['bakingIngredients',
  Counter({'eggs': 94,
           'margarine': 76,
           'flour': 26,
           'yeast': 5,
           'ammonia': 1,
           'baking': -50})],
 ['cakeTypes', Counter({'white': 228, 'pound': 49, 'bunny': 1, 'yellow': -5})],
 ['cheeses', Counter({'cheese': 118, 'mozzarella': 11})],
 ['condiments',
  Counter({'mustard': 49,
           'mayonnaise': 30,
           'ketchup': 18,
           'dressing': 12,
  

In [149]:
pprint(health_diff_2)

[['alcoholicIngredients',
  Counter({'cacao': 4,
           'campari': 1,
           'bourbon': 0,
           'champagne': 0,
           'curacao': -1,
           'sake': -1,
           'cachaca': -1,
           'schnapps': -2,
           'eggnog': -3,
           'vermouth': -4,
           'sherry': -4,
           'bitters': -4,
           'whiskey': -4,
           'sec': -4,
           'ale': -5,
           'beer': -7,
           'tequila': -7,
           'brandy': -8,
           'vodka': -10,
           'liqueur': -14,
           'wine': -17,
           'rum': -19})],
 ['bakingIngredients',
  Counter({'baking': 50,
           'ammonia': -1,
           'yeast': -5,
           'flour': -26,
           'margarine': -76,
           'eggs': -94})],
 ['cakeTypes',
  Counter({'yellow': 5, 'bunny': -1, 'pound': -49, 'white': -228})],
 ['cheeses', Counter({'mozzarella': -11, 'cheese': -118})],
 ['condiments',
  Counter({'vinaigrette': 8,
           'tamari': 5,
           'pesto': 5,
        

In [63]:
# pprint(nonveg_ing_clean)

In [ ]:
def rule_swap_funtion(tuples):
    
    pass

In [65]:
# pprint(veg_ing_clean)

In [ ]:
# Group together larger terms together

In [ ]:
# Function to turn objects into percentages - currently not using 

In [ ]:
# Function for cross examining ingredients for healthy/unhealthy and veg/non veg